In [20]:
import pandas as pd
from xAPIConnector import *
from datetime import datetime
import config

In [21]:
from tqdm import tqdm

In [22]:
client=APIClient()

[2023-05-01 06:55:20,218][connect:74] Socket connected


In [4]:
client.execute(loginCommand(userId=XTB_USER_ID, password='XTB_PASSWORD'))

{'status': True,
 'streamSessionId': '5cf3fcfffe781238-00004ff5-06d6bd7c-3504994c4d95346d-90300fc4'}

In [5]:
symbols=pd.read_csv('/path/to/file/symbols.csv')

In [6]:
symbols

symbol
0   EURAUD
1   AUDNZD
2   GBPMXN
3   GBPJPY
4   USDSEK
5   EURJPY
6   EURMXN
7   CHFPLN
8   USDJPY
9   USDMXN
10  EURRUB
11  EURZAR
12  AUDJPY
13  GBPCAD
14  GBPNZD
15  AUDCHF
16  USDRUB
17  NZDUSD
18  EURRON
19  USDZAR
20  NZDCHF
21  EURSEK
22  USDCLP
23  CHFJPY
24  GBPAUD
25  GBPCHF
26  EURNOK
27  GBPPLN
28  USDCHF
29  CADJPY
30  USDTRY
31  GBPUSD
32  EURCZK
33  EURCNH
34  USDNOK
35  EURCHF
36  USDHUF
37  EURHUF
38  USDIDX
39  GBPZAR
40  AUDUSD
41  USDPLN
42  USDCZK
43  USDCNH
44  NZDJPY
45  EURNZD
46  EURCAD
47  EURGBP
48  USDRON
49  EURUSD
50  EURPLN
51  CHFHUF
52  CADCHF
53  EURTRY
54  AUDCAD
55  USDBRL
56  USDCAD
57  NZDCAD

In [7]:
def history_converter(history):
        
        '''Convert data from dict to pandas df'''
        
        df_dict = history['returnData']['rateInfos']
        digits = history['returnData']['digits']

        df = pd.DataFrame.from_dict(df_dict)

        df['Date'] = df['ctm'].apply(lambda x: datetime.fromtimestamp(x / 1000))
        df['Open'] = df['open'] / (10 ** digits)
        df['Close'] = df['Open'] + df['close'] / (10 ** digits)
        df['High'] = df['Open'] + df['high'] / (10 ** digits)
        df['Low'] = df['Open'] + df['low'] / (10 ** digits)

        df.set_index("Date", inplace=True, drop=True)
        
            
        df = df[['Close']]
        
        return df

In [8]:
start_date = datetime.strptime('2023-03-30', '%Y-%m-%d')
start = int(datetime.timestamp(start_date) * 1000)
end_date=start_date = datetime.strptime('2023-04-27', '%Y-%m-%d')
end=int(datetime.timestamp(end_date) * 1000)
print(start)
args={
    'period':1,
    'symbol':'EURPLN',
    'start':start,
    'end':end
    
}

data=client.commandExecute("getChartRangeRequest", arguments={'info':args})

1680127200000


In [9]:
data

{'status': True,
 'returnData': {'rateInfos': [{'ctm': 1680127260000,
    'ctmString': 'Mar 30, 2023, 12:01:00 AM',
    'open': 46854.0,
    'close': 0.0,
    'high': 0.0,
    'low': 0.0,
    'vol': 1.0},
   {'ctm': 1680127380000,
    'ctmString': 'Mar 30, 2023, 12:03:00 AM',
    'open': 46857.0,
    'close': -5.0,
    'high': 0.0,
    'low': -5.0,
    'vol': 2.0},
   {'ctm': 1680127440000,
    'ctmString': 'Mar 30, 2023, 12:04:00 AM',
    'open': 46855.0,
    'close': 0.0,
    'high': 0.0,
    'low': 0.0,
    'vol': 1.0},
   {'ctm': 1680127620000,
    'ctmString': 'Mar 30, 2023, 12:07:00 AM',
    'open': 46854.0,
    'close': 0.0,
    'high': 0.0,
    'low': 0.0,
    'vol': 1.0},
   {'ctm': 1680128220000,
    'ctmString': 'Mar 30, 2023, 12:17:00 AM',
    'open': 46855.0,
    'close': 0.0,
    'high': 0.0,
    'low': 0.0,
    'vol': 2.0},
   {'ctm': 1680128700000,
    'ctmString': 'Mar 30, 2023, 12:25:00 AM',
    'open': 46855.0,
    'close': 0.0,
    'high': 0.0,
    'low': 0.0,
    '

In [10]:
df_data=history_converter(data)

In [11]:
df_data

Close
Date                       
2023-03-30 00:01:00  4.6854
2023-03-30 00:03:00  4.6852
2023-03-30 00:04:00  4.6855
2023-03-30 00:07:00  4.6854
2023-03-30 00:17:00  4.6855
...                     ...
2023-04-26 23:07:00  4.5801
2023-04-26 23:12:00  4.5819
2023-04-26 23:15:00  4.5817
2023-04-26 23:59:00  4.5816
2023-04-27 00:00:00  4.5807

[24590 rows x 1 columns]

In [12]:
df_all=pd.DataFrame()
for sym in tqdm(symbols['symbol']):
    try:
        start_date = datetime.strptime('2023-03-30', '%Y-%m-%d')
        start = int(datetime.timestamp(start_date) * 1000)
        end_date=start_date = datetime.strptime('2023-04-26', '%Y-%m-%d')
        end=int(datetime.timestamp(end_date) * 1000)
        print(start)
        args={
            'period':1,
            'symbol':sym,
            'start':start,
            'end':end

        }

        data=client.commandExecute("getChartRangeRequest", arguments={'info':args})
        print(data)
        df=history_converter(data)
        df=df.rename(columns={'Close':sym})
        df_all=pd.concat([df_all,df], axis=1)
    except KeyError:
        continue

    

  0%|                                                    | 0/58 [00:00<?, ?it/s]

1680127200000


  2%|▊                                           | 1/58 [00:17<16:22, 17.24s/it]IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)

  3%|█▌                                          | 2/58 [00:34<16:00, 17.15s/it]IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)

  5%|██▎                                         | 3/58 [01:10<23:47, 25.96s/it]IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in orde

{'status': True, 'returnData': {'rateInfos': [{'ctm': 1680156000000, 'ctmString': 'Mar 30, 2023, 8:00:00 AM', 'open': 49515.0, 'close': 3.0, 'high': 9.0, 'low': 0.0, 'vol': 85.0}, {'ctm': 1680156060000, 'ctmString': 'Mar 30, 2023, 8:01:00 AM', 'open': 49518.0, 'close': 15.0, 'high': 20.0, 'low': 0.0, 'vol': 142.0}, {'ctm': 1680156120000, 'ctmString': 'Mar 30, 2023, 8:02:00 AM', 'open': 49534.0, 'close': -3.0, 'high': 1.0, 'low': -11.0, 'vol': 110.0}, {'ctm': 1680156180000, 'ctmString': 'Mar 30, 2023, 8:03:00 AM', 'open': 49531.0, 'close': 0.0, 'high': 25.0, 'low': 0.0, 'vol': 182.0}, {'ctm': 1680156240000, 'ctmString': 'Mar 30, 2023, 8:04:00 AM', 'open': 49532.0, 'close': 4.0, 'high': 12.0, 'low': 0.0, 'vol': 154.0}, {'ctm': 1680156300000, 'ctmString': 'Mar 30, 2023, 8:05:00 AM', 'open': 49535.0, 'close': -5.0, 'high': 0.0, 'low': -5.0, 'vol': 102.0}, {'ctm': 1680156360000, 'ctmString': 'Mar 30, 2023, 8:06:00 AM', 'open': 49530.0, 'close': -5.0, 'high': 0.0, 'low': -6.0, 'vol': 176.0},

 34%|██████████████▊                            | 20/58 [05:22<06:49, 10.77s/it]IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)

 36%|███████████████▌                           | 21/58 [05:38<07:40, 12.44s/it]IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)

 38%|████████████████▎                          | 22/58 [05:54<08:00, 13.35s/it]IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in orde

...

 55%|███████████████████████▋                   | 32/58 [08:16<06:35, 15.22s/it]IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)

 57%|████████████████████████▍                  | 33/58 [08:28<05:52, 14.10s/it]IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)

 59%|█████████████████████████▏                 | 34/58 [08:43<05:50, 14.61s/it]IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in orde

{'status': True, 'returnData': {'rateInfos': [{'ctm': 1680156000000, 'ctmString': 'Mar 30, 2023, 8:00:00 AM', 'open': 45662.0, 'close': 28.0, 'high': 29.0, 'low': 0.0, 'vol': 10.0}, {'ctm': 1680156060000, 'ctmString': 'Mar 30, 2023, 8:01:00 AM', 'open': 45689.0, 'close': -3.0, 'high': 3.0, 'low': -3.0, 'vol': 24.0}, {'ctm': 1680156120000, 'ctmString': 'Mar 30, 2023, 8:02:00 AM', 'open': 45683.0, 'close': -4.0, 'high': 3.0, 'low': -10.0, 'vol': 16.0}, {'ctm': 1680156180000, 'ctmString': 'Mar 30, 2023, 8:03:00 AM', 'open': 45688.0, 'close': 4.0, 'high': 18.0, 'low': 0.0, 'vol': 17.0}, {'ctm': 1680156240000, 'ctmString': 'Mar 30, 2023, 8:04:00 AM', 'open': 45692.0, 'close': -4.0, 'high': 0.0, 'low': -12.0, 'vol': 18.0}, {'ctm': 1680156300000, 'ctmString': 'Mar 30, 2023, 8:05:00 AM', 'open': 45686.0, 'close': 6.0, 'high': 6.0, 'low': -3.0, 'vol': 12.0}, {'ctm': 1680156360000, 'ctmString': 'Mar 30, 2023, 8:06:00 AM', 'open': 45693.0, 'close': -12.0, 'high': 0.0, 'low': -12.0, 'vol': 19.0}, 

 86%|█████████████████████████████████████      | 50/58 [12:33<01:48, 13.53s/it]IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)

 88%|█████████████████████████████████████▊     | 51/58 [12:45<01:30, 13.00s/it]IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)

 90%|██████████████████████████████████████▌    | 52/58 [12:58<01:18, 13.07s/it]IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in orde

{'status': True, 'returnData': {'rateInfos': [{'ctm': 1680177900000, 'ctmString': 'Mar 30, 2023, 2:05:00 PM', 'open': 50953.0, 'close': -81.0, 'high': 7.0, 'low': -82.0, 'vol': 248.0}, {'ctm': 1680177960000, 'ctmString': 'Mar 30, 2023, 2:06:00 PM', 'open': 50871.0, 'close': -37.0, 'high': 0.0, 'low': -45.0, 'vol': 207.0}, {'ctm': 1680178020000, 'ctmString': 'Mar 30, 2023, 2:07:00 PM', 'open': 50835.0, 'close': 25.0, 'high': 44.0, 'low': 0.0, 'vol': 195.0}, {'ctm': 1680178080000, 'ctmString': 'Mar 30, 2023, 2:08:00 PM', 'open': 50861.0, 'close': 48.0, 'high': 49.0, 'low': 0.0, 'vol': 214.0}, {'ctm': 1680178140000, 'ctmString': 'Mar 30, 2023, 2:09:00 PM', 'open': 50907.0, 'close': -1.0, 'high': 5.0, 'low': -7.0, 'vol': 223.0}, {'ctm': 1680178200000, 'ctmString': 'Mar 30, 2023, 2:10:00 PM', 'open': 50907.0, 'close': 41.0, 'high': 54.0, 'low': 0.0, 'vol': 197.0}, {'ctm': 1680178260000, 'ctmString': 'Mar 30, 2023, 2:11:00 PM', 'open': 50944.0, 'close': -30.0, 'high': 5.0, 'low': -31.0, 'vol

 98%|██████████████████████████████████████████▎| 57/58 [14:03<00:12, 12.35s/it]IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)

100%|███████████████████████████████████████████| 58/58 [14:19<00:00, 14.82s/it]IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)




In [13]:
df_all

EURAUD   AUDNZD   GBPMXN   GBPJPY   USDSEK   EURJPY  \
Date                                                                        
2023-03-30 00:01:00  1.62199  1.07439  22.2686  163.467  10.3876  143.933   
2023-03-30 00:02:00  1.62211  1.07430      NaN  163.454  10.3865  143.921   
2023-03-30 00:03:00  1.62202  1.07431  22.2701  163.467  10.3876  143.933   
2023-03-30 00:04:00  1.62216  1.07424  22.2685  163.463  10.3876  143.928   
2023-03-30 00:05:00  1.62197  1.07404  22.2730  163.450  10.3945  143.916   
...                      ...      ...      ...      ...      ...      ...   
2023-04-25 23:56:00  1.65494  1.07895  22.4193  165.932  10.2985  146.712   
2023-04-25 23:57:00  1.65511  1.07895  22.4209  165.932  10.2985  146.731   
2023-04-25 23:58:00  1.65515  1.07897  22.4209  165.932  10.2980  146.731   
2023-04-25 23:59:00  1.65509  1.07895      NaN  165.932  10.2979  146.723   
2023-04-26 00:00:00  1.65578  1.07916  22.4242  166.099  10.3015  146.865   

                      EURMXN  CHFPLN   USDJPY   USDMXN  ...  USDRON   EURUSD  \
Date                                                    ...                    
2023-03-30 00:01:00  19.6083  4.7049  132.722  18.0841  ...     NaN  1.08437   
2023-03-30 00:02:00      NaN  4.7046  132.710  18.0841  ...     NaN  1.08440   
2023-03-30 00:03:00  19.6091  4.7047  132.723  18.0841  ...     NaN  1.08436   
2023-03-30 00:04:00      NaN  4.7049  132.720  18.0841  ...     NaN  1.08436   
2023-03-30 00:05:00  19.6104  4.7049  132.716  18.0855  ...     NaN  1.08435   
...                      ...     ...      ...      ...  ...     ...      ...   
2023-04-25 23:56:00  19.8272  4.6876  133.728      NaN  ...     NaN  1.09726   
2023-04-25 23:57:00  19.8298  4.6876  133.727  18.0652  ...     NaN  1.09735   
2023-04-25 23:58:00  19.8300     NaN  133.727  18.0652  ...     NaN  1.09735   
2023-04-25 23:59:00  19.8301     NaN  133.719      NaN  ...     NaN  1.09737   
2023-04-26 00:00:00  19.8313  4.6876  133.832  18.0711  ...     NaN  1.09745   

                     EURPLN  CHFHUF   CADCHF    EURTRY   AUDCAD  USDBRL  \
Date                                                                      
2023-03-30 00:01:00  4.6854     NaN  0.67714  20.78758  0.90631     NaN   
2023-03-30 00:02:00     NaN  381.51  0.67714  20.78798  0.90629     NaN   
2023-03-30 00:03:00  4.6852  381.56  0.67717  20.78018  0.90633     NaN   
2023-03-30 00:04:00  4.6855  381.56      NaN  20.77878  0.90626     NaN   
2023-03-30 00:05:00     NaN  381.56  0.67706  20.76555  0.90626     NaN   
...                     ...     ...      ...       ...      ...     ...   
2023-04-25 23:56:00  4.5875  385.61  0.65426  21.31366  0.90266     NaN   
2023-04-25 23:57:00  4.5876     NaN  0.65427       NaN  0.90261     NaN   
2023-04-25 23:58:00  4.5878     NaN  0.65424  21.31366      NaN     NaN   
2023-04-25 23:59:00  4.5868     NaN      NaN  21.31366  0.90270     NaN   
2023-04-26 00:00:00  4.5871  385.71  0.65437  21.31023  0.90274     NaN   

                      USDCAD   NZDCAD  
Date                                   
2023-03-30 00:01:00  1.35580      NaN  
2023-03-30 00:02:00  1.35579      NaN  
2023-03-30 00:03:00  1.35579      NaN  
2023-03-30 00:04:00      NaN  0.84353  
2023-03-30 00:05:00  1.35583  0.84351  
...                      ...      ...  
2023-04-25 23:56:00  1.36245  0.83615  
2023-04-25 23:57:00  1.36238  0.83615  
2023-04-25 23:58:00  1.36239  0.83611  
2023-04-25 23:59:00  1.36237  0.83625  
2023-04-26 00:00:00  1.36240  0.83640  

[27119 rows x 56 columns]

In [14]:
df_all.to_csv('/home/slawomir/Portfolio/blog_articles/Choose_the_best_hours/all_1_month.csv')

In [18]:
df_cur=pd.read_csv('/home/slawomir/Portfolio/blog_articles/Choose_the_best_hours/all_1_month.csv', parse_dates=['Date'], index_col='Date')

In [19]:
df_cur

EURAUD   AUDNZD   GBPMXN   GBPJPY   USDSEK   EURJPY  \
Date                                                                        
2023-03-30 00:01:00  1.62199  1.07439  22.2686  163.467  10.3876  143.933   
2023-03-30 00:02:00  1.62211  1.07430      NaN  163.454  10.3865  143.921   
2023-03-30 00:03:00  1.62202  1.07431  22.2701  163.467  10.3876  143.933   
2023-03-30 00:04:00  1.62216  1.07424  22.2685  163.463  10.3876  143.928   
2023-03-30 00:05:00  1.62197  1.07404  22.2730  163.450  10.3945  143.916   
...                      ...      ...      ...      ...      ...      ...   
2023-04-25 23:56:00  1.65494  1.07895  22.4193  165.932  10.2985  146.712   
2023-04-25 23:57:00  1.65511  1.07895  22.4209  165.932  10.2985  146.731   
2023-04-25 23:58:00  1.65515  1.07897  22.4209  165.932  10.2980  146.731   
2023-04-25 23:59:00  1.65509  1.07895      NaN  165.932  10.2979  146.723   
2023-04-26 00:00:00  1.65578  1.07916  22.4242  166.099  10.3015  146.865   

                      EURMXN  CHFPLN   USDJPY   USDMXN  ...  USDRON   EURUSD  \
Date                                                    ...                    
2023-03-30 00:01:00  19.6083  4.7049  132.722  18.0841  ...     NaN  1.08437   
2023-03-30 00:02:00      NaN  4.7046  132.710  18.0841  ...     NaN  1.08440   
2023-03-30 00:03:00  19.6091  4.7047  132.723  18.0841  ...     NaN  1.08436   
2023-03-30 00:04:00      NaN  4.7049  132.720  18.0841  ...     NaN  1.08436   
2023-03-30 00:05:00  19.6104  4.7049  132.716  18.0855  ...     NaN  1.08435   
...                      ...     ...      ...      ...  ...     ...      ...   
2023-04-25 23:56:00  19.8272  4.6876  133.728      NaN  ...     NaN  1.09726   
2023-04-25 23:57:00  19.8298  4.6876  133.727  18.0652  ...     NaN  1.09735   
2023-04-25 23:58:00  19.8300     NaN  133.727  18.0652  ...     NaN  1.09735   
2023-04-25 23:59:00  19.8301     NaN  133.719      NaN  ...     NaN  1.09737   
2023-04-26 00:00:00  19.8313  4.6876  133.832  18.0711  ...     NaN  1.09745   

                     EURPLN  CHFHUF   CADCHF    EURTRY   AUDCAD  USDBRL  \
Date                                                                      
2023-03-30 00:01:00  4.6854     NaN  0.67714  20.78758  0.90631     NaN   
2023-03-30 00:02:00     NaN  381.51  0.67714  20.78798  0.90629     NaN   
2023-03-30 00:03:00  4.6852  381.56  0.67717  20.78018  0.90633     NaN   
2023-03-30 00:04:00  4.6855  381.56      NaN  20.77878  0.90626     NaN   
2023-03-30 00:05:00     NaN  381.56  0.67706  20.76555  0.90626     NaN   
...                     ...     ...      ...       ...      ...     ...   
2023-04-25 23:56:00  4.5875  385.61  0.65426  21.31366  0.90266     NaN   
2023-04-25 23:57:00  4.5876     NaN  0.65427       NaN  0.90261     NaN   
2023-04-25 23:58:00  4.5878     NaN  0.65424  21.31366      NaN     NaN   
2023-04-25 23:59:00  4.5868     NaN      NaN  21.31366  0.90270     NaN   
2023-04-26 00:00:00  4.5871  385.71  0.65437  21.31023  0.90274     NaN   

                      USDCAD   NZDCAD  
Date                                   
2023-03-30 00:01:00  1.35580      NaN  
2023-03-30 00:02:00  1.35579      NaN  
2023-03-30 00:03:00  1.35579      NaN  
2023-03-30 00:04:00      NaN  0.84353  
2023-03-30 00:05:00  1.35583  0.84351  
...                      ...      ...  
2023-04-25 23:56:00  1.36245  0.83615  
2023-04-25 23:57:00  1.36238  0.83615  
2023-04-25 23:58:00  1.36239  0.83611  
2023-04-25 23:59:00  1.36237  0.83625  
2023-04-26 00:00:00  1.36240  0.83640  

[27119 rows x 56 columns]

In [39]:
#function to add spreads to data
def add_spreads(df, symbol):
    symbol = symbol.replace('_', '')
    spreads = pd.read_csv(f'{config.spread_folder}{symbol}_spreads.csv', parse_dates=['date'], index_col='date')
    df['weekday'] = df.index.day_name()
    df['hour'] = df.index.hour
    df = df[df['weekday'] != 'Sunday']
    m_df = pd.merge(df.reset_index(), spreads, how='left', on=['weekday', 'hour']).set_index('Date').fillna(
        method='ffill')
    #m_df = m_df.drop(['weekday', 'hour'], axis=1)
    return m_df

In [23]:
#we choose one day Wednesday to show how it works
df_cur['weekday']=df_cur.index.day_name()

In [24]:
df_cur['hour']=df_cur.index.hour

In [25]:
df_cur

EURAUD   AUDNZD   GBPMXN   GBPJPY   USDSEK   EURJPY  \
Date                                                                        
2023-03-30 00:01:00  1.62199  1.07439  22.2686  163.467  10.3876  143.933   
2023-03-30 00:02:00  1.62211  1.07430      NaN  163.454  10.3865  143.921   
2023-03-30 00:03:00  1.62202  1.07431  22.2701  163.467  10.3876  143.933   
2023-03-30 00:04:00  1.62216  1.07424  22.2685  163.463  10.3876  143.928   
2023-03-30 00:05:00  1.62197  1.07404  22.2730  163.450  10.3945  143.916   
...                      ...      ...      ...      ...      ...      ...   
2023-04-25 23:56:00  1.65494  1.07895  22.4193  165.932  10.2985  146.712   
2023-04-25 23:57:00  1.65511  1.07895  22.4209  165.932  10.2985  146.731   
2023-04-25 23:58:00  1.65515  1.07897  22.4209  165.932  10.2980  146.731   
2023-04-25 23:59:00  1.65509  1.07895      NaN  165.932  10.2979  146.723   
2023-04-26 00:00:00  1.65578  1.07916  22.4242  166.099  10.3015  146.865   

                      EURMXN  CHFPLN   USDJPY   USDMXN  ...  EURPLN  CHFHUF  \
Date                                                    ...                   
2023-03-30 00:01:00  19.6083  4.7049  132.722  18.0841  ...  4.6854     NaN   
2023-03-30 00:02:00      NaN  4.7046  132.710  18.0841  ...     NaN  381.51   
2023-03-30 00:03:00  19.6091  4.7047  132.723  18.0841  ...  4.6852  381.56   
2023-03-30 00:04:00      NaN  4.7049  132.720  18.0841  ...  4.6855  381.56   
2023-03-30 00:05:00  19.6104  4.7049  132.716  18.0855  ...     NaN  381.56   
...                      ...     ...      ...      ...  ...     ...     ...   
2023-04-25 23:56:00  19.8272  4.6876  133.728      NaN  ...  4.5875  385.61   
2023-04-25 23:57:00  19.8298  4.6876  133.727  18.0652  ...  4.5876     NaN   
2023-04-25 23:58:00  19.8300     NaN  133.727  18.0652  ...  4.5878     NaN   
2023-04-25 23:59:00  19.8301     NaN  133.719      NaN  ...  4.5868     NaN   
2023-04-26 00:00:00  19.8313  4.6876  133.832  18.0711  ...  4.5871  385.71   

                      CADCHF    EURTRY   AUDCAD  USDBRL   USDCAD   NZDCAD  \
Date                                                                        
2023-03-30 00:01:00  0.67714  20.78758  0.90631     NaN  1.35580      NaN   
2023-03-30 00:02:00  0.67714  20.78798  0.90629     NaN  1.35579      NaN   
2023-03-30 00:03:00  0.67717  20.78018  0.90633     NaN  1.35579      NaN   
2023-03-30 00:04:00      NaN  20.77878  0.90626     NaN      NaN  0.84353   
2023-03-30 00:05:00  0.67706  20.76555  0.90626     NaN  1.35583  0.84351   
...                      ...       ...      ...     ...      ...      ...   
2023-04-25 23:56:00  0.65426  21.31366  0.90266     NaN  1.36245  0.83615   
2023-04-25 23:57:00  0.65427       NaN  0.90261     NaN  1.36238  0.83615   
2023-04-25 23:58:00  0.65424  21.31366      NaN     NaN  1.36239  0.83611   
2023-04-25 23:59:00      NaN  21.31366  0.90270     NaN  1.36237  0.83625   
2023-04-26 00:00:00  0.65437  21.31023  0.90274     NaN  1.36240  0.83640   

                       weekday  hour  
Date                                  
2023-03-30 00:01:00   Thursday     0  
2023-03-30 00:02:00   Thursday     0  
2023-03-30 00:03:00   Thursday     0  
2023-03-30 00:04:00   Thursday     0  
2023-03-30 00:05:00   Thursday     0  
...                        ...   ...  
2023-04-25 23:56:00    Tuesday    23  
2023-04-25 23:57:00    Tuesday    23  
2023-04-25 23:58:00    Tuesday    23  
2023-04-25 23:59:00    Tuesday    23  
2023-04-26 00:00:00  Wednesday     0  

[27119 rows x 58 columns]

In [73]:
df_wed=df_cur[df_cur['weekday']=='Wednesday']

In [74]:
df_wed

EURAUD   AUDNZD   GBPMXN   GBPJPY   USDSEK   EURJPY  \
Date                                                                        
2023-04-05 00:00:00  1.62224  1.07005  22.6566  164.559  10.2628  144.223   
2023-04-05 00:01:00  1.62232  1.07000  22.6588  164.550      NaN  144.200   
2023-04-05 00:02:00  1.62232  1.06993  22.6588  164.533  10.2628  144.192   
2023-04-05 00:03:00      NaN  1.06989  22.6589  164.528  10.2648  144.188   
2023-04-05 00:04:00  1.62243  1.06986  22.6566  164.527  10.2659  144.190   
...                      ...      ...      ...      ...      ...      ...   
2023-04-19 23:56:00  1.63074  1.08235  22.4317  167.395      NaN  147.467   
2023-04-19 23:57:00  1.63069  1.08255  22.4298  167.410      NaN  147.467   
2023-04-19 23:58:00  1.63062  1.08235  22.4297  167.406  10.3214  147.467   
2023-04-19 23:59:00  1.63118  1.08235  22.4316  167.384  10.3214  147.467   
2023-04-26 00:00:00  1.65578  1.07916  22.4242  166.099  10.3015  146.865   

                      EURMXN  CHFPLN   USDJPY   USDMXN  ...  EURPLN  CHFHUF  \
Date                                                    ...                   
2023-04-05 00:00:00  19.8582  4.7130  131.709  18.1266  ...  4.6772  380.41   
2023-04-05 00:01:00  19.8582  4.7132  131.677  18.1269  ...  4.6772  380.41   
2023-04-05 00:02:00  19.8581  4.7132  131.681  18.1226  ...  4.6772  380.41   
2023-04-05 00:03:00  19.8582  4.7131  131.677  18.1227  ...  4.6772  380.41   
2023-04-05 00:04:00  19.8582  4.7130  131.680      NaN  ...  4.6772  380.41   
...                      ...     ...      ...      ...  ...     ...     ...   
2023-04-19 23:56:00  19.7604     NaN  134.622  18.0352  ...  4.6137     NaN   
2023-04-19 23:57:00  19.7588     NaN  134.636  18.0337  ...  4.6137     NaN   
2023-04-19 23:58:00  19.7588     NaN  134.623  18.0337  ...  4.6137     NaN   
2023-04-19 23:59:00  19.7623  4.6939  134.609  18.0352  ...  4.6137  384.26   
2023-04-26 00:00:00  19.8313  4.6876  133.832  18.0711  ...  4.5871  385.71   

                      CADCHF    EURTRY   AUDCAD  USDBRL   USDCAD   NZDCAD  \
Date                                                                        
2023-04-05 00:00:00  0.67360  21.13537  0.90786     NaN  1.34440  0.84819   
2023-04-05 00:01:00  0.67357  21.13590  0.90785     NaN  1.34448  0.84825   
2023-04-05 00:02:00  0.67363  21.14746  0.90780     NaN  1.34439  0.84821   
2023-04-05 00:03:00  0.67360  21.14699  0.90783     NaN  1.34445  0.84824   
2023-04-05 00:04:00  0.67360  21.14616  0.90773     NaN  1.34445  0.84824   
...                      ...       ...      ...     ...      ...      ...   
2023-04-19 23:56:00  0.66658  21.27226  0.90326     NaN  1.34540  0.83430   
2023-04-19 23:57:00  0.66657       NaN  0.90328     NaN      NaN  0.83429   
2023-04-19 23:58:00  0.66658  21.27226  0.90322     NaN  1.34537  0.83416   
2023-04-19 23:59:00  0.66654  21.27416  0.90324     NaN  1.34544  0.83420   
2023-04-26 00:00:00  0.65437  21.31023  0.90274     NaN  1.36240  0.83640   

                       weekday  hour  
Date                                  
2023-04-05 00:00:00  Wednesday     0  
2023-04-05 00:01:00  Wednesday     0  
2023-04-05 00:02:00  Wednesday     0  
2023-04-05 00:03:00  Wednesday     0  
2023-04-05 00:04:00  Wednesday     0  
...                        ...   ...  
2023-04-19 23:56:00  Wednesday    23  
2023-04-19 23:57:00  Wednesday    23  
2023-04-19 23:58:00  Wednesday    23  
2023-04-19 23:59:00  Wednesday    23  
2023-04-26 00:00:00  Wednesday     0  

[4321 rows x 58 columns]

In [75]:
df_wed_1=df_wed.iloc[:1440]

In [76]:
df_wed_1

EURAUD   AUDNZD   GBPMXN   GBPJPY   USDSEK   EURJPY  \
Date                                                                        
2023-04-05 00:00:00  1.62224  1.07005  22.6566  164.559  10.2628  144.223   
2023-04-05 00:01:00  1.62232  1.07000  22.6588  164.550      NaN  144.200   
2023-04-05 00:02:00  1.62232  1.06993  22.6588  164.533  10.2628  144.192   
2023-04-05 00:03:00      NaN  1.06989  22.6589  164.528  10.2648  144.188   
2023-04-05 00:04:00  1.62243  1.06986  22.6566  164.527  10.2659  144.190   
...                      ...      ...      ...      ...      ...      ...   
2023-04-05 23:55:00  1.62235  1.06375  22.7905  163.536      NaN  143.150   
2023-04-05 23:56:00  1.62251  1.06368  22.7905  163.512      NaN  143.133   
2023-04-05 23:57:00  1.62241  1.06384      NaN  163.507      NaN  143.151   
2023-04-05 23:58:00  1.62238  1.06387      NaN  163.507      NaN  143.133   
2023-04-05 23:59:00      NaN      NaN      NaN  163.453      NaN  143.091   

                      EURMXN  CHFPLN   USDJPY   USDMXN  ...  EURPLN  CHFHUF  \
Date                                                    ...                   
2023-04-05 00:00:00  19.8582  4.7130  131.709  18.1266  ...  4.6772  380.41   
2023-04-05 00:01:00  19.8582  4.7132  131.677  18.1269  ...  4.6772  380.41   
2023-04-05 00:02:00  19.8581  4.7132  131.681  18.1226  ...  4.6772  380.41   
2023-04-05 00:03:00  19.8582  4.7131  131.677  18.1227  ...  4.6772  380.41   
2023-04-05 00:04:00  19.8582  4.7130  131.680      NaN  ...  4.6772  380.41   
...                      ...     ...      ...      ...  ...     ...     ...   
2023-04-05 23:55:00  19.9368     NaN  131.293  18.2959  ...     NaN     NaN   
2023-04-05 23:56:00  19.9368  4.7361  131.280      NaN  ...     NaN     NaN   
2023-04-05 23:57:00  19.9384  4.7361  131.279      NaN  ...     NaN  380.31   
2023-04-05 23:58:00      NaN  4.7361  131.279      NaN  ...  4.6804  380.31   
2023-04-05 23:59:00  19.9384     NaN  131.240      NaN  ...     NaN     NaN   

                      CADCHF    EURTRY   AUDCAD  USDBRL   USDCAD   NZDCAD  \
Date                                                                        
2023-04-05 00:00:00  0.67360  21.13537  0.90786     NaN  1.34440  0.84819   
2023-04-05 00:01:00  0.67357  21.13590  0.90785     NaN  1.34448  0.84825   
2023-04-05 00:02:00  0.67363  21.14746  0.90780     NaN  1.34439  0.84821   
2023-04-05 00:03:00  0.67360  21.14699  0.90783     NaN  1.34445  0.84824   
2023-04-05 00:04:00  0.67360  21.14616  0.90773     NaN  1.34445  0.84824   
...                      ...       ...      ...     ...      ...      ...   
2023-04-05 23:55:00  0.67265       NaN  0.90457     NaN  1.34584  0.85012   
2023-04-05 23:56:00  0.67261       NaN  0.90393     NaN  1.34501  0.84972   
2023-04-05 23:57:00  0.67262  21.00260  0.90426     NaN  1.34464  0.84986   
2023-04-05 23:58:00      NaN  21.00190      NaN     NaN      NaN      NaN   
2023-04-05 23:59:00  0.67275  20.99895  0.90425     NaN  1.34526  0.84985   

                       weekday  hour  
Date                                  
2023-04-05 00:00:00  Wednesday     0  
2023-04-05 00:01:00  Wednesday     0  
2023-04-05 00:02:00  Wednesday     0  
2023-04-05 00:03:00  Wednesday     0  
2023-04-05 00:04:00  Wednesday     0  
...                        ...   ...  
2023-04-05 23:55:00  Wednesday    23  
2023-04-05 23:56:00  Wednesday    23  
2023-04-05 23:57:00  Wednesday    23  
2023-04-05 23:58:00  Wednesday    23  
2023-04-05 23:59:00  Wednesday    23  

[1440 rows x 58 columns]

In [62]:
spreads_df=pd.DataFrame()
hours=df_wed_1.loc[:,'hour']
for symbol in df_wed_1.columns[:-2]:
    df_temp=df_wed_1.loc[:,[symbol,'weekday','hour']]
    df_spreads=add_spreads(df_temp, symbol)
    df_spreads[symbol]=df_spreads['spread']
    df_spreads=df_spreads.loc[:,symbol]
    spreads_df=pd.concat([spreads_df, df_spreads], axis=1)
    
    
    

In [63]:
spreads_df=spreads_df.dropna(axis='columns')

In [64]:
spreads_df.index

Index([2023-04-05 00:00:00, 2023-04-05 00:01:00, 2023-04-05 00:02:00,
       2023-04-05 00:03:00, 2023-04-05 00:04:00, 2023-04-05 00:05:00,
       2023-04-05 00:06:00, 2023-04-05 00:07:00, 2023-04-05 00:08:00,
       2023-04-05 00:09:00,
       ...
       2023-04-05 23:50:00, 2023-04-05 23:51:00, 2023-04-05 23:52:00,
       2023-04-05 23:53:00, 2023-04-05 23:54:00, 2023-04-05 23:55:00,
       2023-04-05 23:56:00, 2023-04-05 23:57:00, 2023-04-05 23:58:00,
       2023-04-05 23:59:00],
      dtype='object', length=1440)

In [65]:
hours

Date
2023-04-05 00:00:00     0
2023-04-05 00:01:00     0
2023-04-05 00:02:00     0
2023-04-05 00:03:00     0
2023-04-05 00:04:00     0
                       ..
2023-04-05 23:55:00    23
2023-04-05 23:56:00    23
2023-04-05 23:57:00    23
2023-04-05 23:58:00    23
2023-04-05 23:59:00    23
Name: hour, Length: 1440, dtype: int64

In [90]:
spreads_df_all=pd.merge(spreads_df, hours, how='left', on=hours.index).rename(columns={'key_0':'Date'}).set_index('Date')

In [91]:
spreads_df_all

EURAUD    AUDNZD   GBPMXN  GBPJPY   USDSEK  EURJPY  \
Date                                                                        
2023-04-05 00:00:00  0.000285  0.000300  0.03590  0.0305  0.02750   0.016   
2023-04-05 00:01:00  0.000285  0.000300  0.03590  0.0305  0.02750   0.016   
2023-04-05 00:02:00  0.000285  0.000300  0.03590  0.0305  0.02750   0.016   
2023-04-05 00:03:00  0.000285  0.000300  0.03590  0.0305  0.02750   0.016   
2023-04-05 00:04:00  0.000285  0.000300  0.03590  0.0305  0.02750   0.016   
...                       ...       ...      ...     ...      ...     ...   
2023-04-05 23:55:00  0.000950  0.001375  0.02435  0.1215  0.03525   0.037   
2023-04-05 23:56:00  0.000950  0.001375  0.02435  0.1215  0.03525   0.037   
2023-04-05 23:57:00  0.000950  0.001375  0.02435  0.1215  0.03525   0.037   
2023-04-05 23:58:00  0.000950  0.001375  0.02435  0.1215  0.03525   0.037   
2023-04-05 23:59:00  0.000950  0.001375  0.02435  0.1215  0.03525   0.037   

                      EURMXN   CHFPLN  USDJPY  USDMXN  ...    EURGBP  \
Date                                                   ...             
2023-04-05 00:00:00  0.01395  0.00655   0.022  0.0248  ...  0.000165   
2023-04-05 00:01:00  0.01395  0.00655   0.022  0.0248  ...  0.000165   
2023-04-05 00:02:00  0.01395  0.00655   0.022  0.0248  ...  0.000165   
2023-04-05 00:03:00  0.01395  0.00655   0.022  0.0248  ...  0.000165   
2023-04-05 00:04:00  0.01395  0.00655   0.022  0.0248  ...  0.000165   
...                      ...      ...     ...     ...  ...       ...   
2023-04-05 23:55:00  0.01915  0.00755   0.037  0.0167  ...  0.000140   
2023-04-05 23:56:00  0.01915  0.00755   0.037  0.0167  ...  0.000140   
2023-04-05 23:57:00  0.01915  0.00755   0.037  0.0167  ...  0.000140   
2023-04-05 23:58:00  0.01915  0.00755   0.037  0.0167  ...  0.000140   
2023-04-05 23:59:00  0.01915  0.00755   0.037  0.0167  ...  0.000140   

                       EURUSD   EURPLN  CHFHUF   CADCHF    EURTRY    AUDCAD  \
Date                                                                          
2023-04-05 00:00:00  0.000090  0.01185   0.925  0.00041  0.057520  0.000255   
2023-04-05 00:01:00  0.000090  0.01185   0.925  0.00041  0.057520  0.000255   
2023-04-05 00:02:00  0.000090  0.01185   0.925  0.00041  0.057520  0.000255   
2023-04-05 00:03:00  0.000090  0.01185   0.925  0.00041  0.057520  0.000255   
2023-04-05 00:04:00  0.000090  0.01185   0.925  0.00041  0.057520  0.000255   
...                       ...      ...     ...      ...       ...       ...   
2023-04-05 23:55:00  0.000385  0.00725   1.380  0.00083  0.022333  0.000770   
2023-04-05 23:56:00  0.000385  0.00725   1.380  0.00083  0.022333  0.000770   
2023-04-05 23:57:00  0.000385  0.00725   1.380  0.00083  0.022333  0.000770   
2023-04-05 23:58:00  0.000385  0.00725   1.380  0.00083  0.022333  0.000770   
2023-04-05 23:59:00  0.000385  0.00725   1.380  0.00083  0.022333  0.000770   

                       USDCAD    NZDCAD  hour  
Date                                           
2023-04-05 00:00:00  0.000260  0.000405     0  
2023-04-05 00:01:00  0.000260  0.000405     0  
2023-04-05 00:02:00  0.000260  0.000405     0  
2023-04-05 00:03:00  0.000260  0.000405     0  
2023-04-05 00:04:00  0.000260  0.000405     0  
...                       ...       ...   ...  
2023-04-05 23:55:00  0.000415  0.001230    23  
2023-04-05 23:56:00  0.000415  0.001230    23  
2023-04-05 23:57:00  0.000415  0.001230    23  
2023-04-05 23:58:00  0.000415  0.001230    23  
2023-04-05 23:59:00  0.000415  0.001230    23  

[1440 rows x 52 columns]

In [68]:
df_wed_1=df_wed_1.loc[:, df_wed_1.columns!='weekday']

In [69]:
df_wed_1

EURAUD   AUDNZD   GBPMXN   GBPJPY   USDSEK   EURJPY  \
Date                                                                        
2023-04-05 00:00:00  1.62224  1.07005  22.6566  164.559  10.2628  144.223   
2023-04-05 00:01:00  1.62232  1.07000  22.6588  164.550      NaN  144.200   
2023-04-05 00:02:00  1.62232  1.06993  22.6588  164.533  10.2628  144.192   
2023-04-05 00:03:00      NaN  1.06989  22.6589  164.528  10.2648  144.188   
2023-04-05 00:04:00  1.62243  1.06986  22.6566  164.527  10.2659  144.190   
...                      ...      ...      ...      ...      ...      ...   
2023-04-05 23:55:00  1.62235  1.06375  22.7905  163.536      NaN  143.150   
2023-04-05 23:56:00  1.62251  1.06368  22.7905  163.512      NaN  143.133   
2023-04-05 23:57:00  1.62241  1.06384      NaN  163.507      NaN  143.151   
2023-04-05 23:58:00  1.62238  1.06387      NaN  163.507      NaN  143.133   
2023-04-05 23:59:00      NaN      NaN      NaN  163.453      NaN  143.091   

                      EURMXN  CHFPLN   USDJPY   USDMXN  ...   EURUSD  EURPLN  \
Date                                                    ...                    
2023-04-05 00:00:00  19.8582  4.7130  131.709  18.1266  ...  1.09555  4.6772   
2023-04-05 00:01:00  19.8582  4.7132  131.677  18.1269  ...  1.09563  4.6772   
2023-04-05 00:02:00  19.8581  4.7132  131.681  18.1226  ...  1.09560  4.6772   
2023-04-05 00:03:00  19.8582  4.7131  131.677  18.1227  ...  1.09557  4.6772   
2023-04-05 00:04:00  19.8582  4.7130  131.680      NaN  ...  1.09553  4.6772   
...                      ...     ...      ...      ...  ...      ...     ...   
2023-04-05 23:55:00  19.9368     NaN  131.293  18.2959  ...  1.09051     NaN   
2023-04-05 23:56:00  19.9368  4.7361  131.280      NaN  ...  1.09053     NaN   
2023-04-05 23:57:00  19.9384  4.7361  131.279      NaN  ...  1.09065     NaN   
2023-04-05 23:58:00      NaN  4.7361  131.279      NaN  ...  1.09058  4.6804   
2023-04-05 23:59:00  19.9384     NaN  131.240      NaN  ...  1.09059     NaN   

                     CHFHUF   CADCHF    EURTRY   AUDCAD  USDBRL   USDCAD  \
Date                                                                       
2023-04-05 00:00:00  380.41  0.67360  21.13537  0.90786     NaN  1.34440   
2023-04-05 00:01:00  380.41  0.67357  21.13590  0.90785     NaN  1.34448   
2023-04-05 00:02:00  380.41  0.67363  21.14746  0.90780     NaN  1.34439   
2023-04-05 00:03:00  380.41  0.67360  21.14699  0.90783     NaN  1.34445   
2023-04-05 00:04:00  380.41  0.67360  21.14616  0.90773     NaN  1.34445   
...                     ...      ...       ...      ...     ...      ...   
2023-04-05 23:55:00     NaN  0.67265       NaN  0.90457     NaN  1.34584   
2023-04-05 23:56:00     NaN  0.67261       NaN  0.90393     NaN  1.34501   
2023-04-05 23:57:00  380.31  0.67262  21.00260  0.90426     NaN  1.34464   
2023-04-05 23:58:00  380.31      NaN  21.00190      NaN     NaN      NaN   
2023-04-05 23:59:00     NaN  0.67275  20.99895  0.90425     NaN  1.34526   

                      NZDCAD  hour  
Date                                
2023-04-05 00:00:00  0.84819     0  
2023-04-05 00:01:00  0.84825     0  
2023-04-05 00:02:00  0.84821     0  
2023-04-05 00:03:00  0.84824     0  
2023-04-05 00:04:00  0.84824     0  
...                      ...   ...  
2023-04-05 23:55:00  0.85012    23  
2023-04-05 23:56:00  0.84972    23  
2023-04-05 23:57:00  0.84986    23  
2023-04-05 23:58:00      NaN    23  
2023-04-05 23:59:00  0.84985    23  

[1440 rows x 57 columns]

In [77]:
df_wed_1.info()

<class 'pandas.core.frame.DataFrame'>
DatetimeIndex: 1440 entries, 2023-04-05 00:00:00 to 2023-04-05 23:59:00
Data columns (total 58 columns):
 #   Column   Non-Null Count  Dtype  
---  ------   --------------  -----  
 0   EURAUD   1426 non-null   float64
 1   AUDNZD   1426 non-null   float64
 2   GBPMXN   1409 non-null   float64
 3   GBPJPY   1429 non-null   float64
 4   USDSEK   1373 non-null   float64
 5   EURJPY   1428 non-null   float64
 6   EURMXN   1420 non-null   float64
 7   CHFPLN   1404 non-null   float64
 8   USDJPY   1434 non-null   float64
 9   USDMXN   1398 non-null   float64
 10  EURZAR   1412 non-null   float64
 11  AUDJPY   1427 non-null   float64
 12  GBPCAD   1419 non-null   float64
 13  GBPNZD   1426 non-null   float64
 14  AUDCHF   1426 non-null   float64
 15  NZDUSD   1425 non-null   float64
 16  EURRON   650 non-null    float64
 17  USDZAR   1332 non-null   float64
 18  NZDCHF   1421 non-null   float64
 19  EURSEK   1364 non-null   float64
 20  USDCLP   303 non

In [79]:
df_wed_1_all=df_wed_1.loc[:, spreads_df.columns]

In [81]:
df_wed_1_all.info()

<class 'pandas.core.frame.DataFrame'>
DatetimeIndex: 1440 entries, 2023-04-05 00:00:00 to 2023-04-05 23:59:00
Data columns (total 51 columns):
 #   Column  Non-Null Count  Dtype  
---  ------  --------------  -----  
 0   EURAUD  1426 non-null   float64
 1   AUDNZD  1426 non-null   float64
 2   GBPMXN  1409 non-null   float64
 3   GBPJPY  1429 non-null   float64
 4   USDSEK  1373 non-null   float64
 5   EURJPY  1428 non-null   float64
 6   EURMXN  1420 non-null   float64
 7   CHFPLN  1404 non-null   float64
 8   USDJPY  1434 non-null   float64
 9   USDMXN  1398 non-null   float64
 10  EURZAR  1412 non-null   float64
 11  AUDJPY  1427 non-null   float64
 12  GBPCAD  1419 non-null   float64
 13  GBPNZD  1426 non-null   float64
 14  AUDCHF  1426 non-null   float64
 15  NZDUSD  1425 non-null   float64
 16  USDZAR  1332 non-null   float64
 17  NZDCHF  1421 non-null   float64
 18  EURSEK  1364 non-null   float64
 19  CHFJPY  1422 non-null   float64
 20  GBPAUD  1427 non-null   float64
 21  G

In [92]:
df_wed_1_all=df_wed_1_all.fillna(method='ffill')

In [94]:
df_wed_1_all.info()

<class 'pandas.core.frame.DataFrame'>
DatetimeIndex: 1440 entries, 2023-04-05 00:00:00 to 2023-04-05 23:59:00
Data columns (total 51 columns):
 #   Column  Non-Null Count  Dtype  
---  ------  --------------  -----  
 0   EURAUD  1440 non-null   float64
 1   AUDNZD  1440 non-null   float64
 2   GBPMXN  1440 non-null   float64
 3   GBPJPY  1440 non-null   float64
 4   USDSEK  1440 non-null   float64
 5   EURJPY  1440 non-null   float64
 6   EURMXN  1440 non-null   float64
 7   CHFPLN  1440 non-null   float64
 8   USDJPY  1440 non-null   float64
 9   USDMXN  1440 non-null   float64
 10  EURZAR  1440 non-null   float64
 11  AUDJPY  1440 non-null   float64
 12  GBPCAD  1440 non-null   float64
 13  GBPNZD  1440 non-null   float64
 14  AUDCHF  1440 non-null   float64
 15  NZDUSD  1440 non-null   float64
 16  USDZAR  1440 non-null   float64
 17  NZDCHF  1440 non-null   float64
 18  EURSEK  1440 non-null   float64
 19  CHFJPY  1440 non-null   float64
 20  GBPAUD  1440 non-null   float64
 21  G

In [95]:
df_wed_1_all.to_csv('/home/slawomir/Portfolio/blog_articles/Choose_the_best_hours/prices.csv')

In [96]:
spreads_df_all.to_csv('/home/slawomir/Portfolio/blog_articles/Choose_the_best_hours/spreads.csv')